In [5]:
import requests
from bs4 import BeautifulSoup
import time
from tqdm.auto import tqdm
import urllib
import pandas as pd
from utils import secrets

In [3]:
secrets = secrets()

In [2]:
def termnum(year, quarter, school='deanza'):
    school = 1 if school.lower() == 'foothill' else 2
    if len(quarter) > 1:
        quarter = {'winter':3, 'spring':4, 'summer':11, 'fall':12}[quarter.lower()]
    else:
        quarter = {'w':3, 's':4, 'm':11, 'f':12}[quarter.lower()]
    year = int(year)
    return year * 100 + quarter * 10 + school

In [3]:
term_code = termnum(input('year: '), input('quarter: '))
payload = {'portalDef':term_code}

In [174]:
s = requests.Session()
r = s.get('https://myportal.fhda.edu/')
r = s.post(r.url, data={'j_username': secrets['canvas_user'],'j_password': secrets['canvas_pass'], '_eventId_proceed':''})
r = s.get('https://ssb-prod.ec.fhda.edu/ssomanager/saml/login?relayState=%2Fc%2Fauth%2FSSB%3Fpkg%3Dhttps%3A%2F%2Fssb-prod.ec.fhda.edu%2FPROD%2Ffhda_uportal.P_DeepLink_Post%3Fp_page%3Dfhda_opencourses.P_Application%26p_payload%3DeyJwb3J0YWxEZWYiOiIyMDIyNDIifQ%3D%3D')

In [175]:
r = s.post(r.url, data={'j_username': secrets['canvas_user'],'j_password': secrets['canvas_pass'], '_eventId_proceed':''})

In [176]:
soup = BeautifulSoup(r.text, 'html.parser')

url = soup.find('form').get('action')
payload = dict()
data = zip([i.get('name') for i in soup.find_all('input', type='hidden')], [i.get('value') for i in soup.find_all('input', type='hidden')])
for i, j in data:
    payload[i] = j
r = s.post(url, data=payload)

In [177]:
soup = BeautifulSoup(r.text, 'html.parser')

url = soup.find('form').get('action')
payload = dict()
data = zip([i.get('name') for i in soup.find_all('input', type='hidden')], [i.get('value') for i in soup.find_all('input', type='hidden')])
for i, j in data:
    payload[i] = j
r = s.post(url, data=payload)

In [10]:
soup = BeautifulSoup(r.text, 'html.parser')
print(soup.prettify())

<p>
 <img src="/fatcow.16/book.png" style="vertical-align: text-top;"/>
 <a href="http://deanza.edu/schedule/" target="_blank">
  Open Course Catalog
 </a>
 |
 <img src="/fatcow.16/calendar_view_month.png" style="vertical-align: text-top;"/>
 <a href="bwskfreg.P_AltPin">
  Add/Drop Classes
 </a>
 <p>
  <b>
   How to Add a Course:
  </b>
  If you see a course you would like to add, write down the CRN for the section you want to register for, and then, click on "Add/Drop Classes" to go the registration page.
  <table class="TblCourses" dept="ACCT" dept-desc="Accounting">
   <tr>
    <th colspan="14">
     <b>
      Accounting - ACCT
     </b>
     <span style="font-weight:normal;">
      <a href="javascript:returnToTop()">
       Back to Top
      </a>
     </span>
    </th>
   </tr>
   <tr>
    <th>
    </th>
    <th>
     Course
    </th>
    <th>
     CRN
     <br/>
     <span style="font-weight:normal;font-size:10px;">
      (click for more detail)
     </span>
    </th>
    <th>
   

In [104]:
dept = 'math'
course = 'd022'
crn = '46117'

In [45]:
data = {'termcode': term_code}
r = requests.post('https://ssb-prod.ec.fhda.edu/PROD/fhda_opencourses.P_GetCourseList', data=data)

In [46]:
soup = BeautifulSoup(r.text, 'html.parser')
tables = soup.find_all('table')
headers = tables[0].findAll('tr')[1] #find row 1, row 0 is useless
headers = [i.text for i in headers] #get text from td items
while '\n' in headers:
    headers.remove('\n') #remove extra headers
for i, j in enumerate(headers):
    if '(' in j:
        idx = j.index('(')
        headers[i] = j[:idx]

In [47]:
depts = [i['dept'] for i in tables] #get all the departments
d = dict() #add departments to dict for table access
for j, i in enumerate(depts):
    d[i] = j

In [48]:
table = tables[d[dept.upper()]] #select table by dept
rows = table.find_all('tr', {'class':'CourseRow'}) #process table rows
frame = [[td.text for td in row.findAll('td')] for row in rows] #get td from each row in rows
frame = pd.DataFrame(frame,columns=headers) 

In [49]:
temp = frame[frame['CRN'] == crn].iloc[0]
if int(temp['Waitlist SlotsAvailable']) > 0 or int(temp['Seats Available']) > 0:
    pass

NameError: name 'crn' is not defined

In [97]:
import re
def fix_course(str):
    str = str.split(' ')[1] #remove dept from string
    str = re.match('D[0-9]*[A-Z.]*', str).group()
    if '.' in str:
        str = str[:-1]
    return str

In [98]:
frame['Course'] = frame['Course'].map(fix_course)

In [1]:
term_code

NameError: name 'term_code' is not defined

In [50]:
table = tables[1] #select table by dept
rows = table.findAll('tr', {'class':'CourseRow'}) #process table rows
frame = [[td.text for td in row.findAll('td')] for row in rows] #get td from each row in rows
frame = pd.DataFrame(frame,columns=headers) 

In [51]:
tables[1]

<table class="TblCourses" dept="ADMJ" dept-desc="Administration of Justice">
<tr>
<th colspan="14">
<b>Administration of Justice - ADMJ</b> <span style="font-weight:normal;"><a href="javascript:returnToTop()">Back to Top</a></span>
</th>
</tr>
<tr>
<th> </th>
<th>Course</th>
<th>CRN<br/><span style="font-weight:normal;font-size:10px;">(click for more detail)</span></th>
<th>Title</th>
<th>Status</th>
<th>Days</th>
<th>Time</th>
<th>Start</th>
<th>End</th>
<th>Room</th>
<th>Campus</th>
<th>Units</th>
<th>Instructor<br/><span style="font-weight:normal;font-size:10px;">(click to e-mail)</span></th>
<th>Seats Available</th>
<th>Waitlist Slots<br/>Available</th>
<th>Waitlist<br/>Capacity</th>
</tr>
<tr class="CourseRow" crs-status="O" crs-type="Z" hotclass="">
<td> </td>
<td>ADMJ D001.01Z</td>
<td><a class="link-course-detail" href="javascript:getCourseDetail('fhda_crscatalog.P_ViewCourse?crse_term=202242&amp;crse_crn=41932&amp;page_mode=full')">41932</a></td>
<td>INTRO TO ADMIN OF JUSTICE<

In [44]:
term_code = 202242